In [1]:
import numpy as np

class NelderMead:
    def __init__(self, func, x0, step_sizes, bounds, alpha=1.0, gamma=2.0, rho=0.5, sigma=0.5):
        self.func = func  # Objective function
        self.bounds = np.array(bounds)
        self.alpha, self.gamma, self.rho, self.sigma = alpha, gamma, rho, sigma
        
        # Initialize simplex
        self.n = len(x0)
        self.simplex = np.zeros((self.n + 1, self.n))
        self.simplex[0] = x0
        for i in range(self.n):
            x = np.array(x0, dtype=float)
            x[i] += step_sizes[i]
            self.simplex[i + 1] = np.clip(x, self.bounds[:, 0], self.bounds[:, 1])
        
        self.f_values = [None] * (self.n + 1)
        self.evaluated = [False] * (self.n + 1)
        self.iteration = 0
    
    def evaluate(self):
        for i in range(self.n + 1):
            if not self.evaluated[i]:
                self.f_values[i] = self.func(self.simplex[i])
                self.evaluated[i] = True
    
    def step(self):
        self.evaluate()
        idx = np.argsort(self.f_values)
        self.simplex = self.simplex[idx]
        self.f_values = [self.f_values[i] for i in idx]
        self.evaluated = [self.evaluated[i] for i in idx]
        
        centroid = np.mean(self.simplex[:-1], axis=0)
        
        # Reflection
        xr = centroid + self.alpha * (centroid - self.simplex[-1])
        xr = np.clip(xr, self.bounds[:, 0], self.bounds[:, 1])
        fr = self.func(xr)
        
        if self.f_values[0] <= fr < self.f_values[-2]:
            self.simplex[-1] = xr
            self.f_values[-1] = fr
            return
        
        if fr < self.f_values[0]:
            # Expansion
            xe = centroid + self.gamma * (xr - centroid)
            xe = np.clip(xe, self.bounds[:, 0], self.bounds[:, 1])
            fe = self.func(xe)
            if fe < fr:
                self.simplex[-1] = xe
                self.f_values[-1] = fe
            else:
                self.simplex[-1] = xr
                self.f_values[-1] = fr
            return
        
        # Contraction
        xc = centroid + self.rho * (self.simplex[-1] - centroid)
        xc = np.clip(xc, self.bounds[:, 0], self.bounds[:, 1])
        fc = self.func(xc)
        
        if fc < self.f_values[-1]:
            self.simplex[-1] = xc
            self.f_values[-1] = fc
            return
        
        # Shrink
        for i in range(1, self.n + 1):
            self.simplex[i] = self.simplex[0] + self.sigma * (self.simplex[i] - self.simplex[0])
            self.simplex[i] = np.clip(self.simplex[i], self.bounds[:, 0], self.bounds[:, 1])
            self.evaluated[i] = False
        
        self.iteration += 1
    
    def optimize(self, max_iters=100):
        for _ in range(max_iters):
            self.step()
        return self.simplex[0], self.f_values[0]

# Test the Nelder-Mead implementation
def objective_function(x):
    return (x[0] - 2) ** 2 + (x[1] - 3) ** 2 + (x[2] + 1) ** 2

x0 = np.array([0.0, 0.0, 0.0])
step_sizes = [1.0, 1.5, 2.0]
bounds = [(-5, 5), (-5, 5), (-5, 5)]

optimizer = NelderMead(objective_function, x0, step_sizes, bounds)
optimal_x, optimal_f = optimizer.optimize(max_iters=200)

print("Optimal x:", optimal_x)
print("Optimal function value:", optimal_f)


Optimal x: [ 2.  3. -1.]
Optimal function value: 8.72480161174439e-28


In [8]:
import math

In [9]:
import numpy as np

class NelderMead:
    def __init__(self, x0, step_sizes, bounds, alpha=1.0, gamma=2.0, rho=0.5, sigma=0.5):
        self.bounds = np.array(bounds)
        self.alpha, self.gamma, self.rho, self.sigma = alpha, gamma, rho, sigma
        
        # Initialize simplex
        self.n = len(x0)
        self.simplex = np.zeros((self.n + 1, self.n))
        self.simplex[0] = x0
        for i in range(self.n):
            x = np.array(x0, dtype=float)
            x[i] += step_sizes[i]
            self.simplex[i + 1] = np.clip(x, self.bounds[:, 0], self.bounds[:, 1])
        
        self.f_values = [math.inf] * (self.n + 1)
        self.evaluated = [False] * (self.n + 1)
        self.iteration = 0
        self.pending_evaluation = None
    
    def get_next_evaluation(self):
        for i in range(self.n + 1):
            if not self.evaluated[i]:
                self.pending_evaluation = i
                return self.simplex[i]
        return None
    
    def set_evaluation_result(self, f_value):
        if self.pending_evaluation is not None:
            self.f_values[self.pending_evaluation] = f_value
            self.evaluated[self.pending_evaluation] = True
            self.pending_evaluation = None
    
    def step(self):
        if any(f is None for f in self.f_values):
            return
        
        idx = np.argsort(self.f_values)
        self.simplex = self.simplex[idx]
        self.f_values = [self.f_values[i] for i in idx]
        self.evaluated = [self.evaluated[i] for i in idx]
        
        centroid = np.mean(self.simplex[:-1], axis=0)
        
        # Reflection
        xr = centroid + self.alpha * (centroid - self.simplex[-1])
        xr = np.clip(xr, self.bounds[:, 0], self.bounds[:, 1])
        self.simplex[-1] = xr
        self.evaluated[-1] = False
    
    def is_converged(self):
        return np.std(self.f_values) < 1e-6

# Test the stepwise Nelder-Mead implementation
def objective_function(x):
    return (x[0] - 2) ** 2 + (x[1] - 3) ** 2 + (x[2] + 1) ** 2

x0 = np.array([0.0, 0.0, 0.0])
step_sizes = [1.0, 1.5, 2.0]
bounds = [(-5, 5), (-5, 5), (-5, 5)]

optimizer = NelderMead(x0, step_sizes, bounds)




In [10]:
optimizer.is_converged()

/ntuzfs/liyang/.local/lib/python3.10/site-packages/numpy/_core/_methods.py:185: RuntimeWarning: invalid value encountered in subtract
  x = asanyarray(arr - arrmean)


np.False_

In [11]:
while not optimizer.is_converged():
    next_eval = optimizer.get_next_evaluation()
    print("next_eval", next_eval)
    if next_eval is not None:
        f_value = objective_function(next_eval)
        optimizer.set_evaluation_result(f_value)
    else:
        optimizer.step()

print("Optimal x:", optimizer.simplex[0])
print("Optimal function value:", optimizer.f_values[0])

next_eval [0. 0. 0.]
next_eval [1. 0. 0.]
next_eval [0.  1.5 0. ]
next_eval [0. 0. 2.]
next_eval None
next_eval [ 0.66666667  1.         -2.        ]
next_eval None
next_eval [ 1.11111111  1.66666667 -1.33333333]
next_eval None
next_eval [ 0.18518519  2.77777778 -2.22222222]
next_eval None
next_eval [ 1.30864198  2.12962963 -3.7037037 ]
next_eval None
next_eval [0.  1.5 0. ]
next_eval None
next_eval [ 1.30864198  2.12962963 -3.7037037 ]
next_eval None
next_eval [0.  1.5 0. ]
next_eval None
next_eval [ 1.30864198  2.12962963 -3.7037037 ]
next_eval None
next_eval [0.  1.5 0. ]
next_eval None
next_eval [ 1.30864198  2.12962963 -3.7037037 ]
next_eval None
next_eval [0.  1.5 0. ]
next_eval None
next_eval [ 1.30864198  2.12962963 -3.7037037 ]
next_eval None
next_eval [0.  1.5 0. ]
next_eval None
next_eval [ 1.30864198  2.12962963 -3.7037037 ]
next_eval None
next_eval [0.  1.5 0. ]
next_eval None
next_eval [ 1.30864198  2.12962963 -3.7037037 ]
next_eval None
next_eval [0.  1.5 0. ]
next_eval 

KeyboardInterrupt: 

In [13]:
class NelderMead:

Step 1: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 2: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 3: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 4: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 5: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 6: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 7: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 8: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 9: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 10: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 11: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 12: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 13: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 14: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 15: Evaluate point [1. 2. 3.]
Objective function value: 14.0
Step 16: Evaluate p

KeyboardInterrupt: 